## According to new data from the restaurant reviewing website Yelp, the share of Chinese restaurants in the top 20 metropolitan areas has been consistently falling. In 2015, an average of 7.3 percent of all restaurants in these areas were Chinese, compared with 6.5 percent in 2019. The share of Chinese restaurants in NYC has been declined just a little bit. In 2015, the figure was about 9 percent and in 2019, the figure became 8.6 percent. The decline in NYC is not obvious compared to the average decline in the top 20 metropolitan areas. Therefore, we can assume the demand of Chinese cuisine is still strong in NYC.

## The purpose of this project is to explore which neighborhood in New York City has less density of Chinese restaurant.

## We use the data from Foursquare.com to explore the density of Chinese restaurant in each neighborhood. In principle, the lower the density is, the lower the competition is. However, the result is for reference only because those who want to open a restaurant should also consider other factors, like the neighborhood's demographic, the average household income, and the security level, etc.

In [2]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
!conda install -c conda-forge geopy --yes # install the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
# import k-means from clustering stage
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
!conda install -c conda-forge folium=0.5.0 --yes # install the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: | 
The environment is inconsistent, please check the package plan carefully
The following packages are causing the inconsistency:
/ 
  - defaults/noarch::ibm-wsrt-py37main-main==custom=1902
  - defaults/noarch::ibm-wsrt-py37main-keep==0.0.0=1902
  - conda-forge/linux-64::pytorch==1.8.0=cpu_py37hafa7651_0
done

# All requested packages already installed.

Solving environment: failed with initial frozen solve. Retrying with flexible solve.
Solving environment: / 
The environment is inconsistent, please check the package plan carefully
The following packages are causing the inconsistency:
- 
  - defaults/noarch::ibm-wsrt-py37main-main==custom=1902
  - defaults/noarch::ibm-wsrt-py37main-keep==0.0.0=1902
  - conda-forge/linux-64::pytorch==1.8.0=cpu_py37hafa7651_0
done

## Package Plan ##

  environment location: /opt/conda/envs/Python-3.7-main

  added / updated specs:
    - folium=0.5.0


The following packages will be downloaded:

    package                    |     

In [3]:
# download and load the dataset of NYC neighborhood
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json

with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

## Tidy Data

In [4]:
# define a new variable that includes feature key
neighborhoods_data = newyork_data['features']

# Tranform the data into a pandas dataframe
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

#loop through the data and fill the dataframe one row at a time
for data in neighborhoods_data:
    #borough = neighborhood_name = data['properties']['borough'] 
    borough = data['properties']['borough'] # data is defined in the beginning of the loop
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [6]:
print(neighborhoods.shape)
neighborhoods.tail()

(306, 4)


Borough  Neighborhood   Latitude  Longitude
301      Manhattan  Hudson Yards  40.756658 -74.000111
302         Queens       Hammels  40.587338 -73.805530
303         Queens     Bayswater  40.611322 -73.765968
304         Queens  Queensbridge  40.756091 -73.945631
305  Staten Island     Fox Hills  40.617311 -74.081740

In [7]:
# make sure that the dataset has all 5 boroughs and 306 neighborhoods.
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


## Acquire NYC data from Foursquare.com

In [8]:
CLIENT_ID = '0WZQC5ZYCJ3K2HJE1XMCSPPYY24TZKU5LA05I0L0A0UHVHIY' # your Foursquare ID
CLIENT_SECRET = 'MAJCBSZR4SAHGL2HNFERENSNIAWRIYL3RX5STMLEM2BQXA0F' # your Foursquare Secret
ACCESS_TOKEN = 'QOEG0C2TDJXPKLRGZSYH5S2RYC2NGEHGUAH3KFUGWHPDD2DN' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 0WZQC5ZYCJ3K2HJE1XMCSPPYY24TZKU5LA05I0L0A0UHVHIY
CLIENT_SECRET:MAJCBSZR4SAHGL2HNFERENSNIAWRIYL3RX5STMLEM2BQXA0F


## Get the latitude and longitude of NYC

In [ ]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

## Create a map of New York with neighborhoods superimposed on top

In [10]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [15]:
neighborhoods

Borough               Neighborhood   Latitude  Longitude
0            Bronx                  Wakefield  40.894705 -73.847201
1            Bronx                 Co-op City  40.874294 -73.829939
2            Bronx                Eastchester  40.887556 -73.827806
3            Bronx                  Fieldston  40.895437 -73.905643
4            Bronx                  Riverdale  40.890834 -73.912585
5            Bronx                Kingsbridge  40.881687 -73.902818
6        Manhattan                Marble Hill  40.876551 -73.910660
7            Bronx                   Woodlawn  40.898273 -73.867315
8            Bronx                    Norwood  40.877224 -73.879391
9            Bronx             Williamsbridge  40.881039 -73.857446
10           Bronx                 Baychester  40.866858 -73.835798
11           Bronx             Pelham Parkway  40.857413 -73.854756
12           Bronx                City Island  40.847247 -73.786488
13           Bronx               Bedford Park  40.870185 -73.885512
14           Bronx         University Heights  40.855727 -73.910416
15           Bronx             Morris Heights  40.847898 -73.919672
16           Bronx                    Fordham  40.860997 -73.896427
17           Bronx               East Tremont  40.842696 -73.887356
18           Bronx                 West Farms  40.839475 -73.877745
19           Bronx               High  Bridge  40.836623 -73.926102
20           Bronx                    Melrose  40.819754 -73.909422
21           Bronx                 Mott Haven  40.806239 -73.916100
22           Bronx                Port Morris  40.801664 -73.913221
23           Bronx                   Longwood  40.815099 -73.895788
24           Bronx                Hunts Point  40.809730 -73.883315
25           Bronx                 Morrisania  40.823592 -73.901506
26           Bronx                  Soundview  40.821012 -73.865746
27           Bronx               Clason Point  40.806551 -73.854144
28           Bronx                Throgs Neck  40.815109 -73.816350
29           Bronx               Country Club  40.844246 -73.824099
30           Bronx                Parkchester  40.837938 -73.856003
31           Bronx         Westchester Square  40.840619 -73.842194
32           Bronx                   Van Nest  40.843608 -73.866299
33           Bronx                Morris Park  40.847549 -73.850402
34           Bronx                    Belmont  40.857277 -73.888452
35           Bronx             Spuyten Duyvil  40.881395 -73.917190
36           Bronx            North Riverdale  40.908543 -73.904531
37           Bronx                 Pelham Bay  40.850641 -73.832074
38           Bronx              Schuylerville  40.826580 -73.826203
39           Bronx             Edgewater Park  40.821986 -73.813885
40           Bronx                Castle Hill  40.819014 -73.848027
41           Bronx                  Olinville  40.871371 -73.863324
42           Bronx             Pelham Gardens  40.862966 -73.841612
43           Bronx                  Concourse  40.834284 -73.915589
44           Bronx                  Unionport  40.829774 -73.850535
45           Bronx                   Edenwald  40.884561 -73.848083
46        Brooklyn                  Bay Ridge  40.625801 -74.030621
47        Brooklyn                Bensonhurst  40.611009 -73.995180
48        Brooklyn                Sunset Park  40.645103 -74.010316
49        Brooklyn                 Greenpoint  40.730201 -73.954241
50        Brooklyn                  Gravesend  40.595260 -73.973471
51        Brooklyn             Brighton Beach  40.576825 -73.965094
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438
54        Brooklyn                   Flatbush  40.636326 -73.958401
55        Brooklyn              Crown Heights  40.670829 -73.943291
56        Brooklyn              East Flatbush  40.641718 -73.936103
57        Brooklyn                 Kensington  40.642382 -73.980421

## Create a function to collect venues data to all the neighborhoods in NYC

In [21]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [22]:
# Now write the code to run the above function on each neighborhood and create a new dataframe called NYC_venues.
NYC_venues = getNearbyVenues(names = neighborhoods['Neighborhood'],
                                 latitudes = neighborhoods['Latitude'],
                                 longitudes = neighborhoods['Longitude'])

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [26]:
print(NYC_venues.shape)
#NYC_venues.shape
NYC_venues.head()

(6129, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896528       -73.844700        Pharmacy  
4            Subway       40.890468       -73.849152  Sandwich Place

## Analyze Each Neighborhood

In [27]:
NYC_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      28                      28   
Annadale                                       9                       9   
Arden Heights                                  4                       4   
Arlington                                      6                       6   
Arrochar                                      22                      22   
Arverne                                       18                      18   
Astoria                                       30                      30   
Astoria Heights                               11                      11   
Auburndale                                    21                      21   
Bath Beach                                    30                      30   
Battery Park City                             30                      30   
Bay Ridge                                     30                      30   
Bay Terrace                                   40                      40   
Baychester                                    21                      21   
Bayside                                       30                      30   
Bayswater                                      2                       2   
Bedford Park                                  30                      30   
Bedford Stuyvesant                            30                      30   
Beechhurst                                    15                      15   
Bellaire                                      15                      15   
Belle Harbor                                  18                      18   
Bellerose                                     19                      19   
Belmont                                       30                      30   
Bensonhurst                                   30                      30   
Bergen Beach                                   6                       6   
Blissville                                    18                      18   
Bloomfield                                     4                       4   
Boerum Hill                                   30                      30   
Borough Park                                  19                      19   
Breezy Point                                   6                       6   
Briarwood                                     10                      10   
Brighton Beach                                30                      30   
Broad Channel                                  6                       6   
Broadway Junction                             17                      17   
Bronxdale                                     12                      12   
Brooklyn Heights                              30                      30   
Brookville                                     1                       1   
Brownsville                                   17                      17   
Bulls Head                                    30                      30   
Bushwick                                      30                      30   
Butler Manor                                   7                       7   
Cambria Heights                               11                      11   
Canarsie                                       5                       5   
Carnegie Hill                                 30                      30   
Carroll Gardens                               30                      30   
Castle Hill                                    6                       6   
Castleton Corners                             14                      14   
Central Harlem                                30                      30   
Charleston                                    25                      25   
Chelsea                                       35                      35   
Chinatown                                     30                      30   

In [30]:
# one hot encoding
nyc_onehot = pd.get_dummies(NYC_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_onehot['Neighborhood'] = NYC_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [nyc_onehot.columns[-1]] + list(nyc_onehot.columns[:-1])
nyc_onehot = nyc_onehot[fixed_columns]

In [32]:
nyc_onehot.shape

(6129, 379)

In [33]:
# Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
nyc_grouped = nyc_onehot.groupby('Neighborhood').mean().reset_index()
nyc_grouped

Neighborhood  Yoga Studio       ATM  Accessories Store  \
0                     Allerton     0.000000  0.000000           0.000000   
1                     Annadale     0.000000  0.000000           0.000000   
2                Arden Heights     0.000000  0.000000           0.000000   
3                    Arlington     0.000000  0.000000           0.000000   
4                     Arrochar     0.000000  0.000000           0.000000   
5                      Arverne     0.000000  0.000000           0.000000   
6                      Astoria     0.000000  0.000000           0.000000   
7              Astoria Heights     0.000000  0.000000           0.000000   
8                   Auburndale     0.000000  0.000000           0.000000   
9                   Bath Beach     0.000000  0.000000           0.000000   
10           Battery Park City     0.000000  0.000000           0.000000   
11                   Bay Ridge     0.000000  0.000000           0.000000   
12                 Bay Terrace     0.000000  0.000000           0.025000   
13                  Baychester     0.000000  0.000000           0.000000   
14                     Bayside     0.000000  0.000000           0.000000   
15                   Bayswater     0.000000  0.000000           0.000000   
16                Bedford Park     0.000000  0.000000           0.000000   
17          Bedford Stuyvesant     0.000000  0.000000           0.000000   
18                  Beechhurst     0.000000  0.000000           0.000000   
19                    Bellaire     0.000000  0.000000           0.000000   
20                Belle Harbor     0.000000  0.000000           0.000000   
21                   Bellerose     0.000000  0.000000           0.000000   
22                     Belmont     0.000000  0.000000           0.000000   
23                 Bensonhurst     0.000000  0.000000           0.000000   
24                Bergen Beach     0.000000  0.000000           0.000000   
25                  Blissville     0.000000  0.000000           0.000000   
26                  Bloomfield     0.000000  0.000000           0.000000   
27                 Boerum Hill     0.066667  0.000000           0.000000   
28                Borough Park     0.000000  0.000000           0.000000   
29                Breezy Point     0.000000  0.000000           0.000000   
30                   Briarwood     0.000000  0.000000           0.000000   
31              Brighton Beach     0.000000  0.000000           0.000000   
32               Broad Channel     0.000000  0.000000           0.000000   
33           Broadway Junction     0.000000  0.000000           0.000000   
34                   Bronxdale     0.000000  0.000000           0.000000   
35            Brooklyn Heights     0.133333  0.000000           0.000000   
36                  Brookville     0.000000  0.000000           0.000000   
37                 Brownsville     0.000000  0.000000           0.000000   
38                  Bulls Head     0.000000  0.000000           0.000000   
39                    Bushwick     0.000000  0.000000           0.000000   
40                Butler Manor     0.000000  0.000000           0.000000   
41             Cambria Heights     0.000000  0.000000           0.000000   
42                    Canarsie     0.000000  0.000000           0.000000   
43               Carnegie Hill     0.033333  0.000000           0.000000   
44             Carroll Gardens     0.000000  0.000000           0.000000   
45                 Castle Hill     0.000000  0.000000           0.000000   
46           Castleton Corners     0.000000  0.000000           0.000000   
47              Central Harlem     0.000000  0.000000           0.000000   
48                  Charleston     0.000000  0.000000           0.000000   
49                     Chelsea     0.000000  0.000000           0.000000   
50                   Chinatown     0.000000  0.000000           0.000000   
51                 City Island     0.000000  0.000000           0.

In [74]:
# Keep only Chinese Restaurant
nyc_grouped_1 = nyc_grouped.filter(['Neighborhood','Chinese Restaurant'], axis = 1)

In [75]:
nyc_grouped_1.head()

Neighborhood  Chinese Restaurant
0       Allerton            0.035714
1       Annadale            0.000000
2  Arden Heights            0.000000
3      Arlington            0.000000
4       Arrochar            0.000000

## Cluster Neighborhoods

In [76]:
# set number of clusters
kclusters = 10
nyc_grouped_clustering = nyc_grouped_1.drop(columns = 'Neighborhood')

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([9, 0, 0, 0, 0, 0, 0, 0, 0, 4], dtype=int32)

In [77]:
nyc_merged.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [78]:
nyc_grouped_1.head()

Neighborhood  Chinese Restaurant
0       Allerton            0.035714
1       Annadale            0.000000
2  Arden Heights            0.000000
3      Arlington            0.000000
4       Arrochar            0.000000

In [79]:
# add clustering labels
nyc_grouped_1.insert(0, 'Cluster Labels', kmeans.labels_)

nyc_merged = neighborhoods

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
nyc_merged = nyc_merged.join(nyc_grouped_1.set_index('Neighborhood'), on='Neighborhood')

nyc_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             0.0   
1   Bronx   Co-op City  40.874294 -73.829939             0.0   
2   Bronx  Eastchester  40.887556 -73.827806             9.0   
3   Bronx    Fieldston  40.895437 -73.905643             0.0   
4   Bronx    Riverdale  40.890834 -73.912585             0.0   

   Chinese Restaurant  
0            0.000000  
1            0.000000  
2            0.041667  
3            0.000000  
4            0.000000

## There is no Chinese restaurant in cluster labels #0

In [87]:
nyc_merged.groupby(by=['Cluster Labels']).mean().sort_values(by = 'Chinese Restaurant')

Latitude  Longitude  Chinese Restaurant
Cluster Labels                                          
0.0             40.695737 -73.959820            0.000000
9.0             40.721947 -73.942825            0.034317
3.0             40.657822 -73.917105            0.051689
4.0             40.694618 -73.939007            0.066481
1.0             40.752444 -73.878210            0.083084
8.0             40.706356 -73.889034            0.105631
6.0             40.774203 -73.813018            0.142165
2.0             40.690775 -73.904986            0.184480
7.0             40.884561 -73.848083            0.250000
5.0             40.603707 -74.132084            0.333333

In [97]:
nyc_merged.head()

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             0.0   
1   Bronx   Co-op City  40.874294 -73.829939             0.0   
2   Bronx  Eastchester  40.887556 -73.827806             9.0   
3   Bronx    Fieldston  40.895437 -73.905643             0.0   
4   Bronx    Riverdale  40.890834 -73.912585             0.0   

   Chinese Restaurant  
0            0.000000  
1            0.000000  
2            0.041667  
3            0.000000  
4            0.000000

## Which neighboorhoods do not have Chinese restaurant? 

In [100]:
nyc_merged.loc[nyc_merged['Cluster Labels'] == 0, nyc_merged.columns[[1] + list(range(5, nyc_merged.shape[1]))]]

Neighborhood  Chinese Restaurant
0                    Wakefield                 0.0
1                   Co-op City                 0.0
3                    Fieldston                 0.0
4                    Riverdale                 0.0
5                  Kingsbridge                 0.0
6                  Marble Hill                 0.0
7                     Woodlawn                 0.0
9               Williamsbridge                 0.0
10                  Baychester                 0.0
12                 City Island                 0.0
14          University Heights                 0.0
15              Morris Heights                 0.0
17                East Tremont                 0.0
20                     Melrose                 0.0
21                  Mott Haven                 0.0
22                 Port Morris                 0.0
23                    Longwood                 0.0
24                 Hunts Point                 0.0
25                  Morrisania                 0.0
27                Clason Point                 0.0
28                 Throgs Neck                 0.0
29                Country Club                 0.0
31          Westchester Square                 0.0
32                    Van Nest                 0.0
33                 Morris Park                 0.0
34                     Belmont                 0.0
35              Spuyten Duyvil                 0.0
37                  Pelham Bay                 0.0
38               Schuylerville                 0.0
40                 Castle Hill                 0.0
44                   Unionport                 0.0
49                  Greenpoint                 0.0
51              Brighton Beach                 0.0
52              Sheepshead Bay                 0.0
53           Manhattan Terrace                 0.0
54                    Flatbush                 0.0
55               Crown Heights                 0.0
57                  Kensington                 0.0
59            Prospect Heights                 0.0
61                Williamsburg                 0.0
62                    Bushwick                 0.0
63          Bedford Stuyvesant                 0.0
64            Brooklyn Heights                 0.0
65                 Cobble Hill                 0.0
66             Carroll Gardens                 0.0
67                    Red Hook                 0.0
68                     Gowanus                 0.0
69                 Fort Greene                 0.0
70                  Park Slope                 0.0
73               Starrett City                 0.0
76                 Mill Island                 0.0
77             Manhattan Beach                 0.0
78                Coney Island                 0.0
81               Dyker Heights                 0.0
82             Gerritsen Beach                 0.0
85                    Sea Gate                 0.0
88   Prospect Lefferts Gardens                 0.0
89                  Ocean Hill                 0.0
91                Bergen Beach                 0.0
92                     Midwood                 0.0
93         Prospect Park South                 0.0
94                  Georgetown                 0.0
95           East Williamsburg                 0.0
97                  South Side                 0.0
98               Ocean Parkway                 0.0
101         Washington Heights                 0.0
103           Hamilton Heights                 0.0
104             Manhattanville                 0.0
105             Central Harlem                 0.0
106                East Harlem                 0.0
107            Upper East Side                 0.0
108                  Yorkville                 0.0
110           Roosevelt Island                 0.0
112             Lincoln Square                 0.0
113                    Clinton                 0.0
115                Murray Hill                 0.0
117          Greenwich Village                 0.0
118               East Village          

## Which neighborhoods have the lowest density of Chinese restaurant?

In [101]:
nyc_merged.loc[nyc_merged['Cluster Labels'] == 1, nyc_merged.columns[[1] + list(range(5, nyc_merged.shape[1]))]]

Neighborhood  Chinese Restaurant
36   North Riverdale            0.076923
41         Olinville            0.083333
43         Concourse            0.086957
154       Douglaston            0.086957
161  Oakland Gardens            0.076923
168  Cambria Heights            0.090909
169         Rosedale            0.083333
186       Ravenswood            0.083333
187       Lindenwood            0.076923
232    Midland Beach            0.076923
270       Mount Hope            0.090909
284    Manor Heights            0.083333
297        Bronxdale            0.083333